# Load packages

In [35]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score, classification_report
from sklearn.preprocessing import StandardScaler

# Load dataset :

In [2]:
data = pd.read_csv('/Users/mac/Desktop/GoMyCode/Electric_cars_dataset.csv')

# Data exploration : 

In [3]:
data.dtypes

ID                                                    object
VIN (1-10)                                            object
County                                                object
City                                                  object
State                                                 object
ZIP Code                                             float64
Model Year                                           float64
Make                                                  object
Model                                                 object
Electric Vehicle Type                                 object
Clean Alternative Fuel Vehicle (CAFV) Eligibility     object
Electric Range                                         int64
Base MSRP                                              int64
Legislative District                                 float64
DOL Vehicle ID                                         int64
Vehicle Location                                      object
Electric Utility        

In [4]:
data.isna().sum()

ID                                                     0
VIN (1-10)                                             0
County                                                 4
City                                                   9
State                                                 11
ZIP Code                                               6
Model Year                                             7
Make                                                   4
Model                                                 13
Electric Vehicle Type                                  0
Clean Alternative Fuel Vehicle (CAFV) Eligibility      0
Electric Range                                         0
Base MSRP                                              0
Legislative District                                 169
DOL Vehicle ID                                         0
Vehicle Location                                     510
Electric Utility                                     722
Expected Price ($1k)           

In [5]:
data.duplicated().sum()

0

In [6]:
data.shape

(64353, 18)

In [7]:
data.corr()

ZIP Code  Model Year  Electric Range  Base MSRP  \
ZIP Code              1.000000   -0.003737       -0.010247  -0.000139   
Model Year           -0.003737    1.000000       -0.080631  -0.218313   
Electric Range       -0.010247   -0.080631        1.000000   0.052901   
Base MSRP            -0.000139   -0.218313        0.052901   1.000000   
Legislative District -0.389266    0.021036        0.042348   0.002203   
DOL Vehicle ID       -0.000843   -0.116860        0.041390   0.004771   

                      Legislative District  DOL Vehicle ID  
ZIP Code                         -0.389266       -0.000843  
Model Year                        0.021036       -0.116860  
Electric Range                    0.042348        0.041390  
Base MSRP                         0.002203        0.004771  
Legislative District              1.000000        0.001431  
DOL Vehicle ID                    0.001431        1.000000

In [8]:
# Rapports de profilage de pandas
Profil = ProfileReport(data,title = 'Rapport SVM')

In [9]:
Profil.to_file("your_report_name.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [10]:
Profil.to_notebook_iframe()

# Handle missing values

In [11]:
data['County'].fillna(data['County'].mode()[0], inplace=True)
data['City'].fillna(data['City'].mode()[0], inplace=True)
data['State'].fillna(data['State'].mode()[0], inplace=True)
data['Model'].fillna(data['Model'].mode()[0], inplace=True)
data['Model Year'].fillna(data['Model Year'].median(), inplace=True)
data['Make'].fillna(data['Make'].mode(), inplace=True)
data['Model'].fillna(data['Model'].mode(), inplace=True)
data['Legislative District'].fillna(data['Legislative District'].mean(), inplace=True)
data['Make'].fillna(data['Make'].mode()[0], inplace=True)
data['Electric Utility'].fillna(data['Electric Utility'].mode()[0], inplace=True)
data['Vehicle Location'].fillna(data['Vehicle Location'].mode()[0], inplace=True)

In [36]:
data.isna().sum()

County                                               0
City                                                 0
State                                                0
Model Year                                           0
Make                                                 0
Model                                                0
Electric Vehicle Type                                0
Clean Alternative Fuel Vehicle (CAFV) Eligibility    0
Electric Range                                       0
Base MSRP                                            0
Legislative District                                 0
Vehicle Location                                     0
Electric Utility                                     0
Expected Price ($1k)                                 0
dtype: int64

# Prétraitement des données :

# Lists of columns to delete

In [13]:
# Liste des colonnes à supprimer
data.drop(columns=["ID", "ZIP Code","VIN (1-10)","DOL Vehicle ID"], axis = 1, inplace=True)

In [14]:
label_encoder = LabelEncoder()
data['County'] = label_encoder.fit_transform(data['County'])
data['City'] = label_encoder.fit_transform(data['County'])
data['State'] = label_encoder.fit_transform(data['State'])
data['Make'] = label_encoder.fit_transform(data['Make'])
data['Model'] = label_encoder.fit_transform(data['Model'])
data['Electric Vehicle Type'] = label_encoder.fit_transform(data['Electric Vehicle Type'])
data['Clean Alternative Fuel Vehicle (CAFV) Eligibility'] = label_encoder.fit_transform(data['Clean Alternative Fuel Vehicle (CAFV) Eligibility'])
data['Vehicle Location'] = label_encoder.fit_transform(data['Vehicle Location'])
data['Electric Utility'] = label_encoder.fit_transform(data['Electric Utility'])
data['Expected Price ($1k)'] = label_encoder.fit_transform(data['Expected Price ($1k)'])

In [15]:
data.dtypes

County                                                 int64
City                                                   int64
State                                                  int64
Model Year                                           float64
Make                                                   int64
Model                                                  int64
Electric Vehicle Type                                  int64
Clean Alternative Fuel Vehicle (CAFV) Eligibility      int64
Electric Range                                         int64
Base MSRP                                              int64
Legislative District                                 float64
Vehicle Location                                       int64
Electric Utility                                       int64
Expected Price ($1k)                                   int64
dtype: object

# Selectionner les variables target et features

In [38]:
X = data.drop('Expected Price ($1k)', axis=1)
y = data['Expected Price ($1k)']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Normalisation/Standardisation des données :

In [39]:
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

# Création et entraînement du modèle SVM :

In [45]:
svm_regressor = SVR(kernel='linear') 
svm_regressor.fit(X_train_scaled, y_train)

SVR(kernel='linear')

# Évaluation du modèle :

In [46]:
y_pred = svm_regressor.predict(X_test_scaled)
mse = mean_squared_error(y_test, y_pred)
r2 = r2_score(y_test, y_pred)

print(f"Accuracy: {accuracy}")
print(f"Mean Squared Error: {mse}")
print(f"R-squared: {r2}")

Accuracy: 0.9578898298500506
Mean Squared Error: 1863.134773809311
R-squared: 0.4458708736385617
